In [2]:
from lets_plot import *
from lets_plot.geo_data import *

import pandas as pd

LetsPlot.setup_html()

The geodata is provided by © OpenStreetMap contributors and is made available here under the Open Database License (ODbL).


In [27]:
income_all = pd.read_csv('../data/US_household_income_2017.csv', encoding='latin-1')
income_all.head(3)

id  State_Code State_Name State_ab          County        City  \
0  1011000           1    Alabama       AL   Mobile County   Chickasaw   
1  1011010           1    Alabama       AL  Barbour County  Louisville   
2  1011020           1    Alabama       AL   Shelby County  Columbiana   

             Place  Type Primary  Zip_Code Area_Code     ALand  AWater  \
0   Chickasaw city  City   place     36611       251  10894952  909156   
1        Clio city  City   place     36048       334  26070325   23254   
2  Columbiana city  City   place     35051       205  44835274  261034   

         Lat        Lon   Mean  Median  Stdev        sum_w  
0  30.771450 -88.079697  38773   30506  33101  1638.260513  
1  31.708516 -85.611039  37725   19528  43789   258.017685  
2  33.191452 -86.615618  54606   31930  57348   926.031000

In [28]:
income_by_state = income_all.groupby("State_Name", as_index=False)["Mean"].mean()
income_by_state.head(3)

State_Name          Mean
0    Alabama  53612.925856
1     Alaska  77670.209524
2    Arizona  62578.071313

In [79]:
# load coordinates of US states in low resolution
states = regions_state('US-48').boundaries(resolution=4)
states.head(3)

request found name                                           geometry
0  Missouri   Missouri  MULTIPOLYGON (((-95.62500 40.58058, -95.53711 ...
1  Nebraska   Nebraska  MULTIPOLYGON (((-95.80078 40.58058, -95.71289 ...
2  Kentucky   Kentucky  MULTIPOLYGON (((-89.56055 36.52729, -89.56055 ...

#### Blank map

In [52]:
map_theme = theme(axis_line="blank", axis_text="blank", axis_title="blank", axis_ticks="blank") + ggsize(900, 400)
ggplot() + geom_map(map=states) + map_theme

In [53]:
ggplot(income_by_state) + geom_map(aes(fill="Mean"), map=states, map_join=["State_Name", "request"]) + map_theme \
    + scale_fill_gradient(low="#007BCD", high="#FE0968", name="Mean income")

In [44]:
scale_fill_gradient2?

In [62]:
# Issue: 'request' in the result is empty.
counties = regions_county(within="US-48").boundaries(resolution=4)
counties.head(3)

request       found name                                           geometry
0          Franklin County  MULTIPOLYGON (((-73.21289 44.77794, -73.21289 ...
1             Comal County  MULTIPOLYGON (((-98.43750 29.76438, -98.52539 ...
2            Travis County  MULTIPOLYGON (((-98.08594 30.52441, -98.08594 ...

In [59]:
ggplot() + geom_map(map=counties) + map_theme

In [67]:
income_by_county = income_all.groupby(["State_Name","County"], as_index=False)["Mean"].mean()
income_by_county.head(3)

State_Name          County          Mean
0    Alabama  Autauga County  53735.557235
1    Alabama  Barbour County  37725.000000
2    Alabama   Blount County  55127.000000

In [81]:
# Issue: 'Internal error', message uninformative
ggplot(income_by_county) + geom_map(aes(fill="Mean"), map=counties, map_join=["County", "request"]) + map_theme \
    + scale_fill_gradient(low="#007BCD", high="#FE0968", name="Mean income", na_value="white")

In [68]:
# Issue: 'map_join' can't join tables just by county name, without state name. 
ggplot(income_by_county) + geom_map(aes(fill="Mean"), map=counties, map_join=["County", "found name"]) + map_theme \
    + scale_fill_gradient(low="#007BCD", high="#FE0968", name="Mean income", na_value="white")

In [80]:
# Issue: batch query takes a lot of time and results with an error. The message is misleading:
# ValueError: Error: Service is down for maintenance
regions_county(income_by_county["County"].tolist(), within=income_by_county["State_Name"].tolist())

ValueError: Error: Service is down for maintenance